# Goal

Collect data needed for power analysis. 
details: https://docs.google.com/document/d/1CBPsPhxxskanm8WXGirxyr-f4QV5eTGDIeOkz7zfsrc/edit

plan:
1. populations - registered users (de, bn, sk)
2. small version (1000) switch
3. edit histories
4. quality filters
    1. de - that's flagged
    <!-- ![image.png](attachment:image.png) -->
    2. bn, sk - at least the unreverted edits / not a vandal message
3. namespace filter
    1. namespace 0
4. first edit on every page
    1. bn, sk - first edit on each page
    2. de - first flagged edit (more details)
4. ------- OUTCOMES, checkpoint: the users edit's we want to count-------
4. get pages views 
4. also return number of edits
4. alse return labor hours (maybe nix)

```
.grat.ssh.env
ssh -N maximilianklein@tools-login.wmflabs.org -L 3310:enwiki.analytics.db.skc.eqiad.wmflabs:3306
```

In [1]:
from civilservant.wikipedia.queries.revisions import get_timestamps_within_range, get_flagged_decision_df, was_reverted
from civilservant.wikipedia.queries.sites import get_new_users
from civilservant.wikipedia.utils import make_cached_df, calc_labour_hours
from civilservant.wikipedia.connections.database import make_wmf_con
from civilservant.wikipedia.connections.api import get_mwapi_session
from datetime import datetime, timedelta
import sqlalchemy
import os
import pandas as pd
import json

import requests

from itertools import product

In [2]:
wmf_con = make_wmf_con()
mwapi_sessions = {'de': get_mwapi_session(lang='de'),
                   'bn': get_mwapi_session(lang='bn'),
                   'sk':get_mwapi_session(lang='sk'),}

# misc_cache_dir = '/data/project/cache/impact-stats-power-analysis'
# if start and end seem backwards to you its because i'm thinking about going backward in time, not travelling forward in it.
PA_REG_END_DT = datetime(2019, 9, 15)
PA_REG_START_DT = datetime(2019,10,1)

In [3]:
@make_cached_df('impact-stats-populations')
def gen_pop(lang):
    mwapi_session = mwapi_sessions[lang]
    pop_l = get_new_users(mwapi_session, start_time=PA_REG_START_DT, end_time=PA_REG_END_DT)
    pop = pd.DataFrame.from_records(pop_l)
    pop['lang']= lang
    return pop

In [4]:
pops = []
for lang in mwapi_sessions.keys():
    pops.append(gen_pop(lang))
pop = pd.concat(pops).reset_index()

In [5]:
pop.tail(10)

index      user_name  user_id   user_registration      action lang
14382    630     G.oorthuys   178254 2019-09-15 10:11:40  autocreate   sk
14383    631     JozefSolus   178253 2019-09-15 09:49:57      create   sk
14384    632     Brankohman   178252 2019-09-15 08:59:25  autocreate   sk
14385    633       Xaalxale   178251 2019-09-15 08:50:28      create   sk
14386    634         Sencha   178250 2019-09-15 08:30:47  autocreate   sk
14387    635     Jbilo93968   178249 2019-09-15 08:12:28  autocreate   sk
14388    636  SSGSS Goku214   178248 2019-09-15 06:52:00  autocreate   sk
14389    637    Juraj.pitak   178247 2019-09-15 06:29:45      create   sk
14390    638       Bearjano   178246 2019-09-15 01:45:52  autocreate   sk
14391    639    Darylgolden   178245 2019-09-15 00:05:16  autocreate   sk

In [6]:
pop.groupby('lang').size()

lang
bn     2487
de    11265
sk      640
dtype: int64

In [7]:
pop = pop[pop['action']=='create']

In [8]:
pop.groupby('lang').size()

lang
bn    1002
de    4650
sk     139
dtype: int64

In [9]:
pop['user_registration_plus_84'] = pop['user_registration'].apply(lambda dt: dt+timedelta(days=84))

In [10]:
@make_cached_df('impact-stats-user-edits')
def get_user_edits(lang, user_name, start_date, end_date):
    return get_timestamps_within_range(lang=lang, start_date=start_date, end_date=end_date, user_name=user_name,
                         con=wmf_con, with_page_id=True, with_rev_id=True)

In [11]:
pop['user_edits_84_reg'] = pop.apply(lambda row: 
                                    get_user_edits(row['lang'],
                                                  row['user_name'], 
                                                  start_date=row['user_registration'],
                                                  end_date=row['user_registration_plus_84']),
                                    axis=1)

In [12]:
pop[pop['user_edits_84_reg'].apply(lambda df: not df.empty)].groupby('lang').size()

lang
bn     217
de    1724
sk      46
dtype: int64

###  narrow down to just flagged / unreverted revs

In [13]:
# pop[pop['user_name']=='Knut Rehders']['user_edits'].apply(lambda df:
#                                                                     get_flagged_decision_df(
#                                                                         rev_ids=list(df['rev_id']),
#                                                                         treatment_date=PA_REG_START_DT,
#                                                                         con=wmf_con,
#                                                                         mwapi_session_de=de_mwapi_session))

In [14]:
# pop[pop['user_name']=='Knut Rehders']

In [15]:
# pop[pop['user_name']=='Paul Mendelssohn'].iloc[0]['user_edits_84_reg']

In [16]:
@make_cached_df('impact-stats-flagged-de')
def de_user_edits_flagged(user_name): #reason not passing in whole edit list is cacheability
    user_edits = pop[pop['user_name']==user_name].iloc[0]['user_edits_84_reg']
    ## idea for how to get the first-flagged time of the page
    ## group user_edits by page
    ## for each page get the flagged decision_df
    ## looking for the first flagging after a user edit, in SQL terms...
    ## in flagged_decision_df get the minimum(flagged_time) that's also greater than the minimum(rev_timestamp) 
    ## concat each by-page-flagged-decision df for returning df
    flagged_decision_dfs = []
    user_edits_pages = user_edits.groupby('rev_page')
    for page_id, user_edits_page in user_edits_pages:
        first_edit_on_page = min(user_edits_page['rev_timestamp'])
        last_edit_on_page = max(user_edits_page['rev_timestamp'])
        rev_ids = list(user_edits_page['rev_id'])
        if len(rev_ids)>0:
            flagged_decision_df = get_flagged_decision_df(rev_ids=rev_ids, treatment_date=last_edit_on_page, 
                            con=wmf_con, mwapi_session_de=mwapi_sessions['de'], first_interesting_rev_ts=first_edit_on_page)
            flagged_decision_dfs.append(flagged_decision_df)
    if len(flagged_decision_dfs)>0:
        return pd.concat(flagged_decision_dfs)
    else:
        return pd.DataFrame()

In [17]:
pm_flags = de_user_edits_flagged('Paul Mendelssohn')

In [18]:
pm_flags.head()

rev_id  rev_page  page_namespace       rev_timestamp  \
0  192858225     22728               0 2019-10-04 21:01:03   
1  192873999     22728               0 2019-10-05 13:27:17   
0  193374412     58729               0 2019-10-22 20:25:21   
1  193375746     58729               0 2019-10-22 21:36:00   
0  193420080   8518702               0 2019-10-24 15:10:59   

         fr_timestamp            max_fr_ts         supremum_ts was_reverted  \
0 2019-10-04 21:03:08  2019-10-04 21:11:29 2019-10-04 21:03:08     no_check   
1 2019-10-05 15:55:39  2019-10-04 21:11:29 2019-10-04 21:03:08     no_check   
0                 NaT  2019-08-26 18:25:37 2019-10-22 22:38:31        False   
1 2019-10-22 22:38:31  2019-08-26 18:25:37 2019-10-22 22:38:31     no_check   
0 2019-10-24 16:29:04  2017-11-17 05:20:53 2019-10-24 16:29:04     no_check   

   flagged  
0     True  
1     True  
0    False  
1     True  
0     True

In [19]:
@make_cached_df('page-id-to-page-title')
def get_page_name_from_page_id(lang, page_id):
    """get page_name from page_id"""
    page_sql = """select page_id, page_title, page_namespace from page where page_id = :page_id;"""
    page_params = {'page_id': page_id}
    # print(rev_flag_params)
    wmf_con.execute(f'use {lang}wiki_p;')
    page_res = pd.read_sql(sqlalchemy.text(page_sql), wmf_con, params=page_params)
    page_res['page_title'] = page_res['page_title'].apply(lambda b:b.decode())
    return page_res


def get_single_page_value_from_page_id(lang, page_id, page_value):
    page_id_df = get_page_name_from_page_id(lang, page_id)
    return page_id_df.iloc[0][page_value]    
    
def get_just_page_title_from_page_id(lang, page_id):
    return get_single_page_value_from_page_id(lang, page_id, 'page_title')

def get_just_page_namespace_from_page_id(lang, page_id):
    return get_single_page_value_from_page_id(lang, page_id, 'page_namespace')
    

In [20]:
@make_cached_df('impact-stats-non-flag-quality')
def user_edits_nonflag_qual(lang, user_name):
    user_edits = pop[(pop['user_name']==user_name) & (pop['lang']==lang)].iloc[0]['user_edits_84_reg']
    rev_ids = list(user_edits['rev_id'])
    page_ids = list(set(list(user_edits['rev_page'])))
    if len(rev_ids)==0:
        return pd.DataFrame()
    else:
        #TODO implement this with the following function
        # TODO this has to return a data-frame that contains the 'page_namespace'
        # see get_just_page_title_from_page_id on how to do that easily
#         {rev_id: was_reverted(rev_id, mwapi_session, radius=3) for rev_id in rev_ids}
#         {page_id: page_ns}
#         return pd.DataFrame(t)
        user_edits['page_namespace'] = user_edits['rev_page'].apply(lambda page_id: 
                                                                    get_just_page_namespace_from_page_id(lang, page_id))
        return user_edits

In [21]:
def get_user_edits_data(lang, user_name):
    # this function is in charge of getting the quality data for a user (de: flagged, others: reverted)
    # plus the namespaces of the edits
    # plus for de the time at which it was first flagged, if so
    if lang=='de':
        return de_user_edits_flagged(user_name)
    elif lang in ('bn', 'sk'):
        return user_edits_nonflag_qual(lang, user_name)

In [22]:
# pop[pop['user_edits_84_reg'].apply(lambda df: len(df)>15)]

In [23]:
pop['user_edits_flagged'] = pop.apply(lambda row: get_user_edits_data(row['lang'], row['user_name']), axis=1)

In [24]:
pop[pop['user_edits_84_reg'].apply(lambda df: not df.empty)].shape, pop[pop['user_edits_flagged'].apply(lambda df: not df.empty)].shape

((1987, 9), (1987, 9))

In [25]:
pop[pop['lang']=='bn' ]
# pop.loc[13737]['lang']
pop.loc[13737]['user_edits_flagged']

rev_timestamp  rev_page   rev_id  page_namespace
0 2019-09-15 03:24:47     10364  3672234               0
1 2019-09-15 03:27:27     10364  3672236               0

### Namespace filter
- TODO move this up one step

In [26]:
def namespace_filter(df):
    if df.empty:
        return df
    namespace_fn = lambda ns: ns%2==0 #even only
    df_ns = df[df['page_namespace'].apply(namespace_fn)]
    return df_ns

pop['user_edits_flagged_ns'] = pop['user_edits_flagged'].apply(namespace_filter)

In [27]:
pop[pop['user_edits_flagged'].apply(lambda df: not df.empty)].shape, pop[pop['user_edits_flagged_ns'].apply(lambda df: not df.empty)].shape

((1987, 10), (1891, 10))

In [28]:
k = pop[(pop['user_edits_flagged'].apply(lambda df: not df.empty)) & (pop['user_edits_flagged_ns'].apply(lambda df: df.empty)) ].iloc[0]['user_edits_flagged']

### first edits on page
- in de, this is going to be the supremum_ts in user_edits_flagged_ns

In [29]:
def first_edit_of_page(df, lang):
    if df.empty:
        return df
    if lang=='de':
        timestamp_col = 'supremum_ts'
    elif lang in ('bn','sk'):
        timestamp_col = 'rev_timestamp'
    first_edits_unnamed = df.groupby('rev_page').agg({timestamp_col:min, 'rev_id':min, 'page_namespace':min})
    first_edits_named = first_edits_unnamed.rename(columns={timestamp_col:'rev_timestamp'})
    # if 'rev_timestamp is null', don't return the row
    first_edits = first_edits_named[pd.notnull(first_edits_named['rev_timestamp'])]
    return first_edits
        
pop['user_edits_flagged_ns_pageunique'] = pop.apply(lambda row: first_edit_of_page(row['user_edits_flagged_ns'], row['lang']), axis=1)

In [30]:
pop[pop['user_name']=='Paul Mendelssohn']['user_edits_flagged_ns_pageunique'].iloc[0]

rev_timestamp     rev_id  page_namespace
rev_page                                               
22728    2019-10-04 21:03:08  192858225               0
58729    2019-10-22 22:38:31  193374412               0
8518702  2019-10-24 16:29:04  193420080               0
10974163 2019-10-05 00:27:49  192746320               0
10975348 2019-10-18 18:44:24  192774184               0
10994556 2019-10-31 19:22:41  193211996               0
11001183 2019-11-12 15:52:29  193375687               0
11001881 2019-11-12 21:02:11  193392726               0

In [31]:
some_unique = pop[pop['user_edits_flagged_ns'].apply(len) != pop['user_edits_flagged_ns_pageunique'].apply(len)]

In [32]:
some_unique.iloc[0]['user_edits_flagged_ns']

rev_id  rev_page  page_namespace       rev_timestamp  \
0  192747829   5834370               0 2019-09-30 22:56:38   
1  192747940   5834370               0 2019-09-30 23:05:01   
2  192748102   5834370               0 2019-09-30 23:18:01   
3  192748134   5834370               0 2019-09-30 23:21:15   

         fr_timestamp           max_fr_ts         supremum_ts was_reverted  \
0                 NaT 2019-08-27 09:14:48 2019-11-14 18:02:44        False   
1                 NaT 2019-08-27 09:14:48 2019-11-14 18:02:44        False   
2                 NaT 2019-08-27 09:14:48 2019-11-14 18:02:44        False   
3 2019-11-14 18:02:44 2019-08-27 09:14:48 2019-11-14 18:02:44     no_check   

   flagged  
0    False  
1    False  
2    False  
3     True

In [33]:
some_unique.iloc[0]['user_edits_flagged_ns_pageunique']

rev_timestamp     rev_id  page_namespace
rev_page                                               
5834370  2019-11-14 18:02:44  192747829               0

### get pagenames from page id
- page view api only works on page names

In [34]:
def add_page_names(lang, df):
    if df.empty:
        return df
    df = df.reset_index()
    df['page_title'] = df['rev_page'].apply(lambda page_id: get_just_page_title_from_page_id(lang, page_id))
    return df
    
pop['user_edits_flagged_ns_pageunique_pname'] = pop.apply(lambda row: add_page_names(row['lang'], row['user_edits_flagged_ns_pageunique']), axis=1)

In [35]:
pop[pop['user_edits_flagged_ns_pageunique_pname'].apply(lambda df: len(df)>5)].iloc[3]['user_edits_flagged_ns_pageunique_pname']

rev_page       rev_timestamp     rev_id  page_namespace  \
0    850215 2019-09-28 21:42:51  192682835              10   
1    850254 2019-09-28 21:44:16  192682486              10   
2    853011 2019-09-28 21:43:39  192682570              10   
3    861555 2019-09-28 21:41:47  192682404              10   
4    862241 2019-09-28 20:20:21  192682613              10   
5   8386479 2019-09-28 19:32:54  192682412               0   
6  10000998 2019-09-28 19:22:22  192682849               0   
7  10422840 2019-09-28 19:42:26  192682498               0   
8  10971595 2019-09-28 20:10:58  192683514               0   

                                          page_title  
0        Navigationsleiste_Weltmeister_im_100-m-Lauf  
1        Navigationsleiste_Weltmeister_im_Weitsprung  
2        Navigationsleiste_Weltmeister_im_Hammerwurf  
3  Navigationsleiste_Weltmeisterinnen_im_10.000-m...  
4   Navigationsleiste_Weltmeisterinnen_im_Hammerwurf  
5                                       Sifan_Hassan  
6                                  Christian_Coleman  
7                                        Tajay_Gayle  
8                                       DeAnna_Price

## outcome variables
- befores = 7, 14, 28
- afters = 7, 14, 28, 56, 84
- offsets = 2, 4

- edits.before.BEFORE
- page.views.AFTER
- pages.edited.AFTER
- OFFSET.week.retention.AFTER
- OFFSET.week.labor.AFTER
- OFFSET.week.edit.AFTER


In [36]:
# make before and after datetimes
BEFORE_DAYS = [7, 14, 28]
AFTER_DAYS = [7, 14, 28, 56, 84]
RETENTION_WEEK_OFFSETS = [2, 4]

In [37]:
for bd in BEFORE_DAYS:
    col_name = f'user_registration_minus_{bd}'
    pop[col_name] = pop['user_registration'].apply(lambda reg: reg-timedelta(days=bd))

for ad in AFTER_DAYS:
    col_name = f'user_registration_plus_{ad}'
    pop[col_name] = pop['user_registration'].apply(lambda reg: reg+timedelta(days=ad))

In [38]:
pop.head(1)

index        user_name  user_id   user_registration  action lang  \
0      0  ReginaMusselman  3306898 2019-09-30 23:54:15  create   de   

  user_registration_plus_84  \
0       2019-12-23 23:54:15   

                                   user_edits_84_reg  \
0  Empty DataFrame
Columns: [rev_timestamp, rev_p...   

                      user_edits_flagged  \
0  Empty DataFrame
Columns: []
Index: []   

                   user_edits_flagged_ns  \
0  Empty DataFrame
Columns: []
Index: []   

        user_edits_flagged_ns_pageunique  \
0  Empty DataFrame
Columns: []
Index: []   

  user_edits_flagged_ns_pageunique_pname user_registration_minus_7  \
0  Empty DataFrame
Columns: []
Index: []       2019-09-23 23:54:15   

  user_registration_minus_14 user_registration_minus_28  \
0        2019-09-16 23:54:15        2019-09-02 23:54:15   

  user_registration_plus_7 user_registration_plus_14  \
0      2019-10-07 23:54:15       2019-10-14 23:54:15   

  user_registration_plus_28 user_registration_plus_56  
0       2019-10-28 23:54:15       2019-11-25 23:54:15

### pageviews

In [39]:
import requests
import urllib.parse

In [40]:
datetime(2019,2,2,5).strftime('%Y%m%d%H')

'2019020205'

In [41]:
def get_pageview_article(lang, article, start_dt, end_dt):
    project=f'{lang}.wikipedia'
    access='all-access'
    agent='all-agents'
    granularity='daily'
    start=start_dt.strftime('%Y%m%d%H')
    end=end_dt.strftime('%Y%m%d%H')
    q_str = f'metrics/pageviews/per-article/{project}/{access}/{agent}/{article}/{granularity}/{start}/{end}'
    base_url = 'https://wikimedia.org/api/rest_v1'
    req_str = f'{base_url}/{q_str}'
    res = requests.get(req_str)
    if res.ok:
        return res
    elif res.json()['type']=='https://mediawiki.org/wiki/HyperSwitch/errors/not_found':
        raise NameError
    else:
        print(f"Error on {res.json()}")
        raise ValueError(res)

In [42]:
# get_pageview_article('de', 'Schlaf', datetime(2019,1,1), datetime(2019,2,1)).json()

In [43]:
# @make_cached_df('pageviews')
def get_pageviews_article_df(lang, article, start_dt, end_dt):
    zero_df =  pd.DataFrame([{'views':0}])
    if start_dt>end_dt:
        print(f"Timing Error on {lang}:{article}. s:{start_dt} e:{end_dt}")
        return zero_df
    try:
        res = get_pageview_article(lang, article, start_dt, end_dt)
        res_df = pd.DataFrame(res.json()['items'])
    except NameError:
        res_df = zero_df
    return res_df

def get_pageviews_article_sum(lang, article, start_dt, end_dt):
    article_quoted = urllib.parse.quote(article, safe='') # yes we do want to quote forwardslashes
    res_df = get_pageviews_article_df(lang, article_quoted, start_dt, end_dt)
    article_sum = res_df['views'].sum()
    return article_sum

def get_pageviews_articles(lang, pageunique_df, end_date):
    pageunique_df['pageviews'] = pageunique_df.apply(lambda row: get_pageviews_article_sum(lang,
                                                                                        row['page_title'],
                                                                                          row['rev_timestamp'],
                                                                                          end_date),
                                                                                           axis=1)
    return pageunique_df

def get_pageviews_articles_sum(lang, df, end_date):
    if df.empty:
        return float('nan')
    else:
        pva = get_pageviews_articles(lang, df, end_date)
        total_pageviews = pva['pageviews'].sum()
        return total_pageviews

In [44]:
# pop_s = pop[:200]

In [45]:
for ad in AFTER_DAYS:
    reg_col_name = f'user_registration_plus_{ad}'
    pv_col_name = f'page_views_{ad}'
    pop[pv_col_name] = pop.apply(lambda row: get_pageviews_articles_sum(row['lang'],
                                                                            row['user_edits_flagged_ns_pageunique_pname'],
                                                                                 row[reg_col_name]
                                                                                ) , axis=1)

2020-09-21 15:02:58,207 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:02:58,497 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/Verdienstorden_der_Bundesrepublik_Deutschland/daily/2019100101/2019100723 HTTP/1.1" 200 222
2020-09-21 15:02:58,515 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:02:58,706 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/Node-RED/daily/2019100412/2019100723 HTTP/1.1" 200 611
Timing Error on de:Friedrich_Fechner. s:2019-11-14 18:02:44 e:2019-10-07 22:51:43
2020-09-21 15:02:58,724 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:02:58,903 

2020-09-21 15:03:02,297 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:03:02,480 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/Neukirchen-Vluyn/daily/2019093021/2019100715 HTTP/1.1" 200 203
Timing Error on de:Unabh%C3%A4ngige_W%C3%A4hlergemeinschaft_des_Kreises_Mettmann. s:2019-11-14 18:00:49 e:2019-10-07 15:18:49
Timing Error on de:Bruno_Steinhoff. s:2019-11-14 08:51:45 e:2019-10-07 15:08:32
Timing Error on de:Tycho_Brahe. s:2019-12-01 14:31:19 e:2019-10-07 14:58:16
Timing Error on de:Fluorchlorkohlenwasserstoffe. s:2019-11-28 17:02:50 e:2019-10-07 14:58:16
Timing Error on de:Zeitdilatation. s:2019-12-10 16:46:25 e:2019-10-07 14:58:16
Timing Error on de:Badisches_Landesmuseum. s:2019-12-01 14:40:22 e:2019-10-07 14:58:16
Timing Error on de:Thomas-Mann-Gymnasium_Stutensee. s:2019-12-11 07:06:12 e:2019-10-07

2020-09-21 15:03:05,792 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/Cosmo_%26_Wanda_%E2%80%93_Wenn_Elfen_helfen/daily/2019093012/2019100712 HTTP/1.1" 200 224
2020-09-21 15:03:05,812 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:03:06,009 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/San_Francisco_Shock/daily/2019093017/2019100712 HTTP/1.1" 200 None
2020-09-21 15:03:06,026 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:03:06,171 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/Paul_Koutnik/daily/2019093012/2019100712

2020-09-21 15:03:09,566 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:03:09,753 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/Ananas/daily/2019093009/2019100709 HTTP/1.1" 200 196
Timing Error on de:Katja_Kessler. s:2019-10-07 11:08:43 e:2019-10-07 09:32:05
2020-09-21 15:03:09,775 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:03:09,956 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/Susanne_Betancor/daily/2019093009/2019100709 HTTP/1.1" 200 202
Timing Error on de:Libanesische_Fu%C3%9Fballnationalmannschaft_der_Frauen. s:2019-11-08 06:00:06 e:2019-10-07 09:21:08
Timing Error on de:Megachurch. s:2019-11-20 17:11:40 e:2019-10-07 0

2020-09-21 15:03:13,524 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:03:13,736 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/Arno_Geiger/daily/2019100206/2019100619 HTTP/1.1" 200 772
Timing Error on de:Liste_der_Baudenkmale_in_Wriedel. s:2019-10-11 07:36:06 e:2019-10-06 19:06:21
2020-09-21 15:03:13,754 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:03:13,942 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/de.wikipedia/all-access/all-agents/Marilyn_Monroe/daily/2019092919/2019100619 HTTP/1.1" 200 204
2020-09-21 15:03:13,956 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:03:14,149 production: u

...

2020-09-21 15:51:02,952 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:03,166 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/%C5%A0imon_Val%C3%B3/daily/2019101818/2019122118 HTTP/1.1" 200 303
2020-09-21 15:51:03,183 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:03,399 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/Boldogk%C5%91v%C3%A1ralja/daily/2019100307/2019122118 HTTP/1.1" 200 None
2020-09-21 15:51:03,412 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:03,605 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/res

2020-09-21 15:51:07,805 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:08,080 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/Jozef_Figura/daily/2019112111/2019122118 HTTP/1.1" 200 265
2020-09-21 15:51:08,096 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:08,274 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/Michal_%C4%8Cahoj/daily/2019112114/2019122118 HTTP/1.1" 200 267
2020-09-21 15:51:08,287 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:08,477 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/page

2020-09-21 15:51:12,529 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:12,765 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/Milan_Michal_Harminc/daily/2019092712/2019122012 HTTP/1.1" 200 None
2020-09-21 15:51:12,779 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:12,974 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/Sedlisk%C3%A1/daily/2019092704/2019122004 HTTP/1.1" 200 None
2020-09-21 15:51:12,996 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:13,198 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metric

2020-09-21 15:51:17,155 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:17,341 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/Bene/daily/2019092318/2019121618 HTTP/1.1" 200 None
2020-09-21 15:51:17,356 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:17,590 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/Dietylamid_kyseliny_lysergovej/daily/2019092316/2019121616 HTTP/1.1" 200 None
2020-09-21 15:51:17,610 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:17,806 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metri

2020-09-21 15:51:22,095 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:22,304 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/Michalovce/daily/2019091813/2019121112 HTTP/1.1" 200 None
2020-09-21 15:51:22,323 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:22,544 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metrics/pageviews/per-article/sk.wikipedia/all-access/all-agents/FK_Dubnica_nad_V%C3%A1hom/daily/2019091809/2019121109 HTTP/1.1" 200 None
2020-09-21 15:51:22,562 production: urllib3.connectionpool: 28610: DEBUG: Starting new HTTPS connection (1): wikimedia.org:443
2020-09-21 15:51:22,747 production: urllib3.connectionpool: 28610: DEBUG: https://wikimedia.org:443 "GET /api/rest_v1/metr

### pages edited

In [46]:
def get_pages_edited(df, end_date, ns_fn):
    if df.empty:
        return 0
    else:
        df_date = df[df['rev_timestamp'] < end_date]
        df_date_ns = df_date[df_date['page_namespace'].apply(ns_fn)]
        return len(df_date_ns)

In [47]:
for ad in AFTER_DAYS:
    ns_fn = lambda ns: ns%2==0
    reg_col_name = f'user_registration_plus_{ad}'
    pv_col_name = f'pages_edited_{ad}'
    pop[pv_col_name] = pop.apply(lambda row: get_pages_edited(row['user_edits_flagged_ns_pageunique_pname'],
                                                                                 row[reg_col_name],
                                                                                 ns_fn
                                                                                ) , axis=1)

In [48]:
pop[pop['user_edits_flagged_ns_pageunique_pname'].apply(lambda df: len(df)>5)].iloc[3]['user_edits_flagged_ns_pageunique_pname']

rev_page       rev_timestamp     rev_id  page_namespace  \
0    850215 2019-09-28 21:42:51  192682835              10   
1    850254 2019-09-28 21:44:16  192682486              10   
2    853011 2019-09-28 21:43:39  192682570              10   
3    861555 2019-09-28 21:41:47  192682404              10   
4    862241 2019-09-28 20:20:21  192682613              10   
5   8386479 2019-09-28 19:32:54  192682412               0   
6  10000998 2019-09-28 19:22:22  192682849               0   
7  10422840 2019-09-28 19:42:26  192682498               0   
8  10971595 2019-09-28 20:10:58  192683514               0   

                                          page_title  pageviews  
0        Navigationsleiste_Weltmeister_im_100-m-Lauf          0  
1        Navigationsleiste_Weltmeister_im_Weitsprung          0  
2        Navigationsleiste_Weltmeister_im_Hammerwurf          0  
3  Navigationsleiste_Weltmeisterinnen_im_10.000-m...          0  
4   Navigationsleiste_Weltmeisterinnen_im_Hammerwurf          0  
5                                       Sifan_Hassan      22850  
6                                  Christian_Coleman      14926  
7                                        Tajay_Gayle       2832  
8                                       DeAnna_Price       1317

In [49]:
pop[pop['user_edits_flagged_ns_pageunique_pname'].apply(lambda df: len(df)>5)]

index               user_name  user_id   user_registration  action  \
380      380            Visual Binno  3306518 2019-09-30 13:27:27  create   
412      412        Paul Mendelssohn  3306485 2019-09-30 12:45:50  create   
896      896          Saraworkaholic  3305999 2019-09-29 18:51:36  create   
1589    1589             Sprinta2019  3305304 2019-09-28 18:57:49  create   
1846    1846  Friedrich von Bogislaw  3305047 2019-09-28 11:56:41  create   
...      ...                     ...      ...                 ...     ...   
12342   1077           Toushik Islam   251134 2019-09-24 08:53:28  create   
13316   2051           Mahuya Marjit   250135 2019-09-18 04:17:28  create   
13808     56              Hisgeomaps   178828 2019-09-29 12:18:43  create   
13834     82                 Ratkovo   178802 2019-09-28 18:56:30  create   
13958    206               Simfox004   178678 2019-09-25 19:54:33  create   

      lang user_registration_plus_84  \
380     de       2019-12-23 13:27:27   
412     de       2019-12-23 12:45:50   
896     de       2019-12-22 18:51:36   
1589    de       2019-12-21 18:57:49   
1846    de       2019-12-21 11:56:41   
...    ...                       ...   
12342   bn       2019-12-17 08:53:28   
13316   bn       2019-12-11 04:17:28   
13808   sk       2019-12-22 12:18:43   
13834   sk       2019-12-21 18:56:30   
13958   sk       2019-12-18 19:54:33   

                                       user_edits_84_reg  \
380             rev_timestamp  rev_page     rev_id
0 ...   
412             rev_timestamp  rev_page     rev_id
0 ...   
896             rev_timestamp  rev_page     rev_id
0 ...   
1589            rev_timestamp  rev_page     rev_id
0 ...   
1846             rev_timestamp  rev_page     rev_id
0...   
...                                                  ...   
12342           rev_timestamp  rev_page   rev_id
0  2...   
13316          rev_timestamp  rev_page   rev_id
0 201...   
13808           rev_timestamp  rev_page   rev_id
0  2...   
13834            rev_timestamp  rev_page   rev_id
0  ...   
13958           rev_timestamp  rev_page   rev_id
0  2...   

                                      user_edits_flagged  \
380          rev_id  rev_page  page_namespace       r...   
412           rev_id  rev_page  page_namespace       ...   
896          rev_id  rev_page  page_namespace       r...   
1589         rev_id  rev_page  page_namespace       r...   
1846          rev_id  rev_page  page_namespace       ...   
...                                                  ...   
12342           rev_timestamp  rev_page   rev_id  pag...   
13316          rev_timestamp  rev_page   rev_id  page...   
13808           rev_timestamp  rev_page   rev_id  pag...   
13834            rev_timestamp  rev_page   rev_id  pa...   
13958           rev_timestamp  rev_page   rev_id  pag...   

                                   user_edits_flagged_ns  ... page_views_7  \
380          rev_id  rev_page  page_namespace       r...  ...       7936.0   
412           rev_id  rev_page  page_namespace       ...  ...        749.0   
896          rev_id  rev_page  page_namespace       r...  ...       6365.0   
1589         rev_id  rev_page  page_namespace       r...  ...      31940.0   
1846          rev_id  rev_page  page_namespace       ...  ...      32474.0   
...                                                  ...  ...          ...   
12342           rev_timestamp  rev_page   rev_id  pag...  ...          0.0   
13316          rev_timestamp  rev_page   rev_id  page...  ...        699.0   
13808           rev_timestamp  rev_page   rev_id  pag...  ...        440.0   
13834            rev_timestamp  rev_page   rev_id  pa...  ...        438.0   
13958           rev_timestamp  rev_page   rev_id  pag...  ...        273.0   

      page_views_14 page_views_28 page_views_56 page_views_84 pages_edited_7  \
380         13423.0       24148.0       47731.0       71491.0              4   
412          1939.0        5888.0       20026.0       35314.0 

In [50]:
pop.head()

index         user_name  user_id   user_registration  action lang  \
0       0   ReginaMusselman  3306898 2019-09-30 23:54:15  create   de   
4       4      Knut Rehders  3306894 2019-09-30 23:39:27  create   de   
11     11     KnudHollander  3306887 2019-09-30 23:05:29  create   de   
13     13             JFFJF  3306885 2019-09-30 22:51:43  create   de   
18     18  Tadas Meskauskis  3306880 2019-09-30 22:40:58  create   de   

   user_registration_plus_84  \
0        2019-12-23 23:54:15   
4        2019-12-23 23:39:27   
11       2019-12-23 23:05:29   
13       2019-12-23 22:51:43   
18       2019-12-23 22:40:58   

                                    user_edits_84_reg  \
0   Empty DataFrame
Columns: [rev_timestamp, rev_p...   
4           rev_timestamp  rev_page     rev_id
0 2...   
11          rev_timestamp  rev_page     rev_id
0 2...   
13          rev_timestamp  rev_page     rev_id
0 2...   
18  Empty DataFrame
Columns: [rev_timestamp, rev_p...   

                                   user_edits_flagged  \
0               Empty DataFrame
Columns: []
Index: []   
4         rev_id  rev_page  page_namespace       r...   
11        rev_id  rev_page  page_namespace       r...   
13        rev_id  rev_page  page_namespace       r...   
18              Empty DataFrame
Columns: []
Index: []   

                                user_edits_flagged_ns  ... page_views_7  \
0               Empty DataFrame
Columns: []
Index: []  ...          NaN   
4         rev_id  rev_page  page_namespace       r...  ...       8916.0   
11        rev_id  rev_page  page_namespace       r...  ...        726.0   
13        rev_id  rev_page  page_namespace       r...  ...          0.0   
18              Empty DataFrame
Columns: []
Index: []  ...          NaN   

   page_views_14 page_views_28 page_views_56 page_views_84 pages_edited_7  \
0            NaN           NaN           NaN           NaN              0   
4        14899.0       28223.0       55247.0       83878.0              1   
11        1380.0        2566.0        5454.0        8779.0              1   
13           0.0           0.0          58.0          92.0              0   
18           NaN           NaN           NaN           NaN              0   

   pages_edited_14 pages_edited_28 pages_edited_56  pages_edited_84  
0                0               0               0                0  
4                1               1               1                1  
11               1               1               1                1  
13               0               0               1                1  
18               0               0               0                0  

[5 rows x 29 columns]

In [51]:
pop[pop['page_views_7']>0]

index          user_name  user_id   user_registration  action lang  \
4          4       Knut Rehders  3306894 2019-09-30 23:39:27  create   de   
11        11      KnudHollander  3306887 2019-09-30 23:05:29  create   de   
24        24    TheBenutzername  3306874 2019-09-30 22:14:37  create   de   
47        47      Jan Bielefeld  3306851 2019-09-30 21:33:33  create   de   
104      104         MeepMeep99  3306794 2019-09-30 20:36:41  create   de   
...      ...                ...      ...                 ...     ...  ...   
14303    551             Sl svk   178333 2019-09-17 10:20:02  create   sk   
14335    583  Igazat mondtam 01   178301 2019-09-16 16:36:21  create   sk   
14358    606             Xoshuo   178278 2019-09-16 03:17:41  create   sk   
14372    620      Peter Radoczi   178264 2019-09-15 15:07:07  create   sk   
14383    631         JozefSolus   178253 2019-09-15 09:49:57  create   sk   

      user_registration_plus_84  \
4           2019-12-23 23:39:27   
11          2019-12-23 23:05:29   
24          2019-12-23 22:14:37   
47          2019-12-23 21:33:33   
104         2019-12-23 20:36:41   
...                         ...   
14303       2019-12-10 10:20:02   
14335       2019-12-09 16:36:21   
14358       2019-12-09 03:17:41   
14372       2019-12-08 15:07:07   
14383       2019-12-08 09:49:57   

                                       user_edits_84_reg  \
4              rev_timestamp  rev_page     rev_id
0 2...   
11             rev_timestamp  rev_page     rev_id
0 2...   
24             rev_timestamp  rev_page     rev_id
0 2...   
47             rev_timestamp  rev_page     rev_id
0 2...   
104            rev_timestamp  rev_page     rev_id
0 2...   
...                                                  ...   
14303          rev_timestamp  rev_page   rev_id
0 201...   
14335          rev_timestamp  rev_page   rev_id
0 201...   
14358          rev_timestamp  rev_page   rev_id
0 201...   
14372          rev_timestamp  rev_page   rev_id
0 201...   
14383           rev_timestamp  rev_page   rev_id
0  2...   

                                      user_edits_flagged  \
4            rev_id  rev_page  page_namespace       r...   
11           rev_id  rev_page  page_namespace       r...   
24           rev_id  rev_page  page_namespace       r...   
47           rev_id  rev_page  page_namespace       r...   
104          rev_id  rev_page  page_namespace       r...   
...                                                  ...   
14303          rev_timestamp  rev_page   rev_id  page...   
14335          rev_timestamp  rev_page   rev_id  page...   
14358          rev_timestamp  rev_page   rev_id  page...   
14372          rev_timestamp  rev_page   rev_id  page...   
14383           rev_timestamp  rev_page   rev_id  pag...   

                                   user_edits_flagged_ns  ... page_views_7  \
4            rev_id  rev_page  page_namespace       r...  ...       8916.0   
11           rev_id  rev_page  page_namespace       r...  ...        726.0   
24           rev_id  rev_page  page_namespace       r...  ...        168.0   
47           rev_id  rev_page  page_namespace       r...  ...      16185.0   
104          rev_id  rev_page  page_namespace       r...  ...       1967.0   
...                                                  ...  ...          ...   
14303          rev_timestamp  rev_page   rev_id  page...  ...       2545.0   
14335          rev_timestamp  rev_page   rev_id  page...  ...         55.0   
14358          rev_timestamp  rev_page   rev_id  page...  ...        526.0   
14372          rev_timestamp  rev_page   rev_id  page...  ...        142.0   
14383           rev_timestamp  rev_page   rev_id  pag...  ...         90.0   

      page_views_14 page_views_28 page_views_56 page_views_84 pages_edited_7  \
4           14899.0       28223.0       55247.0       83878.0              1   
11           1380.0        2566.0        5454.0        8779.0              1   
24            489.0        1460.0        3

### retention measures
- need reg_plus 

In [52]:
@make_cached_df('impact-stats-user-edits-retention')
def de_user_edits_ret(lang, user_name, start_date, end_date):
    return get_timestamps_within_range(lang=lang, start_date=start_date, end_date=end_date, user_name=user_name,
                         con=wmf_con, with_page_id=False, with_rev_id=False)

In [53]:
maximum_days_needed = 84 + 21 + 7 + 28 # treatment is 84 days after reg, then 21 days (4wk ret), then 7 edits window (4wk ret), then 28 days (catlab retention measure extra)  
maximum_days_needed_td = timedelta(maximum_days_needed)
pop[f'user_edits_{maximum_days_needed}_reg'] = pop.apply(lambda row:
                                    de_user_edits_ret(row['lang'],
                                                    row['user_name'], 
                                                  start_date=row['user_registration'],
                                                  end_date=row['user_registration']+maximum_days_needed_td),
                                    axis=1)

In [54]:
def k_week_retention_n(k, n, user_reg, ts_df):
    '''k is week number after treatment
    n is the days after registration that we are treating
    '''
    treatment_dt = user_reg + timedelta(days=n)
    retention_week_offset = timedelta(weeks=k) - timedelta(weeks=1) # if its' 2 week retenion, we want edits starting in the second week
    start_dt = treatment_dt + retention_week_offset 
    retention_extra_window = timedelta(days=28)
    end_dt = start_dt + timedelta(weeks=1) + retention_extra_window
    
    window_ts_df =  ts_df[(ts_df['rev_timestamp'] > start_dt)  & (ts_df['rev_timestamp'] <= end_dt)]
    return True if len(window_ts_df)>0 else False

In [55]:
for k, n in product(RETENTION_WEEK_OFFSETS, AFTER_DAYS):
    col_name = f'{k}_week_retention_{n}'
    print(f'working on {col_name}')
    pop[col_name] = pop.apply(
        lambda row: k_week_retention_n(k, n, row['user_registration'], row['user_edits_140_reg']) 
                                      ,axis=1)

working on 2_week_retention_7
working on 2_week_retention_14
working on 2_week_retention_28
working on 2_week_retention_56
working on 2_week_retention_84
working on 4_week_retention_7
working on 4_week_retention_14
working on 4_week_retention_28
working on 4_week_retention_56
working on 4_week_retention_84


In [56]:
pop[['2_week_retention_7',
'2_week_retention_14',
'2_week_retention_28',
'2_week_retention_56',
'2_week_retention_84',]].sum()

2_week_retention_7     214
2_week_retention_14    175
2_week_retention_28    148
2_week_retention_56    115
2_week_retention_84     98
dtype: int64

In [57]:
pop[['4_week_retention_7',
'4_week_retention_14',
'4_week_retention_28',
'4_week_retention_56',
'4_week_retention_84',]].sum()

4_week_retention_7     166
4_week_retention_14    148
4_week_retention_28    137
4_week_retention_56     97
4_week_retention_84    103
dtype: int64

### edit measures
k_week_labor_n
k_week_edits_n

In [58]:
def editlabor_window(k, n, user_reg, ts_df):
    start_dt = user_reg + timedelta(days=n)
    end_dt = start_dt + timedelta(weeks=k)
    window_ts_df =  ts_df[(ts_df['rev_timestamp'] > start_dt)  & (ts_df['rev_timestamp'] <= end_dt)]
    return window_ts_df



def k_week_editlabor_n(k, n, editlabor, user_reg, ts_df):
    window_ts_df = editlabor_window(k, n, user_reg, ts_df)
    
    if editlabor=='edits':
        return len(window_ts_df)
    
    elif editlabor=='labor':
        if len(window_ts_df)==0:
            return 0
        else:
            window_dts = [pd.to_datetime(np_dt) for np_dt in window_ts_df['rev_timestamp'].values]
            window_labor_hours = calc_labour_hours(window_dts)
            return window_labor_hours    

In [59]:
for editlabor, k, n in product(('edits', 'labor'), RETENTION_WEEK_OFFSETS, AFTER_DAYS,):
    col_name = f'{k}_week_{editlabor}_{n}'
    print(f'workin on {col_name}')
    pop[col_name] = pop.apply(lambda row:
                                    k_week_editlabor_n(k, n, editlabor, row['user_registration'], row['user_edits_140_reg'])
                                    , axis=1)

workin on 2_week_edits_7
workin on 2_week_edits_14
workin on 2_week_edits_28
workin on 2_week_edits_56
workin on 2_week_edits_84
workin on 4_week_edits_7
workin on 4_week_edits_14
workin on 4_week_edits_28
workin on 4_week_edits_56
workin on 4_week_edits_84
workin on 2_week_labor_7
workin on 2_week_labor_14
workin on 2_week_labor_28
workin on 2_week_labor_56
workin on 2_week_labor_84
workin on 4_week_labor_7
workin on 4_week_labor_14
workin on 4_week_labor_28
workin on 4_week_labor_56
workin on 4_week_labor_84


In [60]:
pop[['2_week_edits_7',
'2_week_edits_14',
'2_week_edits_28',
'2_week_edits_56',
'2_week_edits_84',]].sum()

2_week_edits_7     1436
2_week_edits_14     995
2_week_edits_28     648
2_week_edits_56     651
2_week_edits_84     761
dtype: int64

In [61]:
pop[['2_week_labor_7',
'2_week_labor_14',
'2_week_labor_28',
'2_week_labor_56',
'2_week_labor_84',]].sum()

2_week_labor_7     167.572778
2_week_labor_14    110.533056
2_week_labor_28     84.166111
2_week_labor_56     92.267222
2_week_labor_84    105.745278
dtype: float64

## Output

In [62]:
pop.columns

Index(['index', 'user_name', 'user_id', 'user_registration', 'action', 'lang',
       'user_registration_plus_84', 'user_edits_84_reg', 'user_edits_flagged',
       'user_edits_flagged_ns', 'user_edits_flagged_ns_pageunique',
       'user_edits_flagged_ns_pageunique_pname', 'user_registration_minus_7',
       'user_registration_minus_14', 'user_registration_minus_28',
       'user_registration_plus_7', 'user_registration_plus_14',
       'user_registration_plus_28', 'user_registration_plus_56',
       'page_views_7', 'page_views_14', 'page_views_28', 'page_views_56',
       'page_views_84', 'pages_edited_7', 'pages_edited_14', 'pages_edited_28',
       'pages_edited_56', 'pages_edited_84', 'user_edits_140_reg',
       '2_week_retention_7', '2_week_retention_14', '2_week_retention_28',
       '2_week_retention_56', '2_week_retention_84', '4_week_retention_7',
       '4_week_retention_14', '4_week_retention_28', '4_week_retention_56',
       '4_week_retention_84', '2_week_edits_7', '2_we

In [63]:
pop = pop.rename(columns={'action':'create_type'})
#OUTCOLS = ['user_name', 'user_id', 'user_registration', 'create_type', 'page_views_7', 'page_views_14', 'page_views_28', 'page_views_56', 'page_views_84']
SKIPCOLS = ['user_edits', 'user_edits_140_reg', 'user_edits_84_reg', 'user_registration_plus_84', 'user_edits_84_reg', 'user_edits_flagged',
       'user_edits_flagged_ns', 'user_edits_flagged_ns_pageunique',
       'user_edits_flagged_ns_pageunique_pname', 'user_registration_minus_7',
       'user_registration_minus_14', 'user_registration_minus_28',
       'user_registration_plus_7', 'user_registration_plus_14',
       'user_registration_plus_28', 'user_registration_plus_56', 'skip_cols']
OUTCOLS = [c for c in pop.columns if c not in SKIPCOLS]
R_OUTCOLS = [c.replace('_','.') for c in OUTCOLS]
pop_out = pop.copy()
pop_out = pop_out[OUTCOLS]
pop_out.columns = R_OUTCOLS
pop_out_fname = f'/home/paprika/Tresors/CivilServant/projects/wikipedia-integration/impact-stats/newcomer_pageviews_{"_".join(mwapi_sessions.keys())}.csv'
pop_out.to_csv(pop_out_fname, index=False)

In [64]:
pop_out_fname

'/home/paprika/Tresors/CivilServant/projects/wikipedia-integration/impact-stats/newcomer_pageviews_de_bn_sk.csv'